# Computing The $H^1$-error

Goal is to compute the error $\|\nabla (u-u_h)\|$ and study convergence for $h\to 0$. We usually do not know the exact solution. Therefore, we start by specifying an analytic solution 
$$
u(x,y) = \sin(2\pi)\sin(\pi y)
$$
and by computing the right hand side using the equation
$$
f(x,y) = -\Delta u(x,y)
$$

## Starting point is the last script

We cleaned it up a little bit and now define functions to specify dirichlet data and right hand side

In [ ]:
from ngsolve import *
from ngsolve.webgui import Draw


def F(x,y):   # definition of the right hand side 
    return 2*cos(x)*sin(y)

def G(x,y):   # definition of the dirichlet data function
    return cos(x)*sin(y)


def solve(fes,F,G): # solves -Delta u = F, u=G on boundary

    u,v = fes.TnT()  # short form for 'test and trial'
    
    gu = GridFunction(fes) 
    gu.Set(G(x,y),BND)
    
    A = BilinearForm(grad(u)*grad(v)*dx).Assemble()
    f = LinearForm(F(x,y)*v*dx).Assemble()
    r = f.vec - A.mat * gu.vec
    
    gu.vec.data += A.mat.Inverse(freedofs=fes.FreeDofs()) * r
    return gu


## Initialize: Mesh & Finite element space, test and trian functions
hmax = 0.1 # setting the mesh size
mesh = Mesh(unit_square.GenerateMesh(maxh=hmax))
fes = H1(mesh, order=2, dirichlet="left|top|bottom|right")

gu = solve(fes,F,G)
Draw(gu,mesh) # plot


### --> Task

Compute the right hand side $f(x,y) = -\Delta u(x,y)$ for the function $u(x,y) = sin(2\pi x)sin(\pi y)$ and implement it.

Solve the problem
$$
-\Delta u = f\text{ in }\Omega,\quad u=0\text{ on }\partial\Omega
$$
with the right hand side you just calculated and check visually if the solution looks like you expect it. 

## Computing the error

To compute errors we can define an object storing the exact solution $u(x,y)$

In [ ]:
exact = sin(2*pi*x)*sin(pi*y)   # The object is called a coefficientFunction


exact_x = exact.Diff(x)   # you can take derivatives of these functions
exact_y = exact.Diff(y)

We can plot the exact solution and also its derivative

In [ ]:
Draw(exact,mesh)     # plot of the solution 
Draw(exact_x,mesh)   # .. of the x-derivative
Draw(exact_y,mesh)   # .. of the y-derivative
Draw(exact-gu,mesh) # .. of the error

## --> Task. Is the error small?

Check that the error is small $<0.1$ and getting very small if you make the mesh smaller. Before the error is not going to zero, something is wrong! Correct your script.


#### 2. Computing integrals

We can easily compute Integrals over the domain 

In [ ]:
Integrate(exact,mesh)   # Just the integral over the exact solution (average)

l2error = Integrate((exact-gu)*(exact-gu),mesh)  # the l2-error
# the h1 error
h1error = Integrate((exact_x-grad(gu)[0])*(exact_y-grad(gu)[1]),mesh)
print('Mesh size h={}'.format(hmax))
print('L2 error        || u-u_h || = {}'.format(sqrt(l2error)))
print('H1 error || nabla(u-u_h) || = {}'.format(sqrt(h1error)))

## --> Task

Study the convergence of the finite element method for h=0.1, 0.05, 0.025 using order 1, order 2 and order 3 finite elements. 

Write a loop to automatically solve the problem on a sequence of meshes and print the mesh size and the L2 and H1 error as a table. 

Verify the order of convergence